In [1]:
from __future__ import annotations

from dataclasses import dataclass
from typing import List, Tuple
import numpy as np

from core.models import Message, MessageId, ThreadId, SpaceId
from core.stores import EmbeddingStore, MembershipStore, MessageStore, ThreadStore
from core.interfaces import Formatter, Embedder, Reducer, Clusterer, ThreadRepComputer, Assigner, UpdateStrategy, ThreadLabeler

import re
import datetime
import numpy as np
import pandas as pd

import logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

## Defining the components for the processor

In [24]:
from huggingface_hub import hf_hub_download

model_path = hf_hub_download(
    repo_id="bartowski/Llama-3.2-3B-Instruct-GGUF",
    filename="Llama-3.2-3B-Instruct-Q4_K_M.gguf",
    local_dir="./models"  # Downloads to a 'models' folder in your current directory
)

print(f"Model downloaded to: {model_path}")

Model downloaded to: models\Llama-3.2-3B-Instruct-Q4_K_M.gguf


In [ ]:
from core.strategies import ContextWindowFormatter, MiniLMEmbedder, UMAPReducer, HDBSCANClusterer, LlamaThreadLabeler, CentroidThreadRepComputer

In [25]:
messages = MessageStore()
threads = ThreadStore()
memberships = MembershipStore()
embeddings = EmbeddingStore()

formatter = ContextWindowFormatter(window_back=2, window_fwd=1, time_threshold_minutes=10, repeat_center=2)
embedder = MiniLMEmbedder("all-MiniLM-L6-v2")
reducer = UMAPReducer(n_neighbors=30, n_components=5, min_dist=0.0, metric="cosine", random_state=42)
clusterer = HDBSCANClusterer(min_cluster_size=30, min_samples=3, metric="euclidean", cluster_selection_method="eom")
labeler = LlamaThreadLabeler(
    model_path="models/Llama-3.2-3B-Instruct-Q4_K_M.gguf",
    n_ctx=2048,
    max_msg_chars=300
)

thread_rep = CentroidThreadRepComputer(memberships=memberships, embeddings=embeddings, msg_space="msg:full")

INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cpu
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: all-MiniLM-L6-v2
llama_context: n_ctx_per_seq (2048) < n_ctx_train (131072) -- the full capacity of the model will not be utilized


## Formatting raw data

In [ ]:
from utils import raw2df

In [27]:
clean_df = raw2df('data/chats/whatsapp_chat_data_test.txt', '12hr')

## Populating message store

In [28]:
def load_from_df(df_clean) -> None:
    msgs = []
    for i, row in df_clean.iterrows():
        msgs.append(
            Message(
                id=f"m{i}",
                timestamp=row["date_time"].to_pydatetime() if hasattr(row["date_time"], "to_pydatetime") else row["date_time"],
                user=str(row["user"]),
                text=str(row["message"]),
            )
        )
    messages.add(msgs)

load_from_df(clean_df)

## Creating and running the main processor

In [29]:
from core.processor import ChatProcessor

processor = ChatProcessor(
    messages=messages,
    threads=threads,
    memberships=memberships,
    embeddings=embeddings,
    embedder=embedder,
    reducer=reducer,
    clusterer=clusterer,
    thread_rep_computer=thread_rep,
    assigner=NoOpAssigner(),
    update_strategy=NoOpUpdateStrategy(),
    formatter=formatter,
    labeler=labeler,
)

In [30]:
processor.run_batch()

INFO:core.processor:run_batch: start
INFO:core.processor:run_batch: messages=13655
INFO:core.processor:run_batch: formatting messages
INFO:core.processor:run_batch: formatted texts=13655
INFO:core.processor:run_batch: embedding texts
Batches: 100%|██████████| 427/427 [00:56<00:00,  7.54it/s]
INFO:core.processor:run_batch: embeddings shape=(13655, 384) dtype=float32
INFO:core.processor:run_batch: stored msg embeddings space=msg:full count=13655
INFO:core.processor:run_batch: reducing embeddings
C:\Users\saba\Desktop\projects\Nexus\.venv\Lib\site-packages\umap\umap_.py:1952: UserWarning:

n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.

INFO:core.processor:run_batch: reduced shape=(13655, 5) dtype=float32
INFO:core.processor:run_batch: stored cluster embeddings space=msg:cluster count=13655
INFO:core.processor:run_batch: clustering
INFO:core.processor:run_batch: clustering done clusters=96 noise_msgs=4553
INFO:core.processor:_labels_to_threads: start 

DEBUG: Raw LLM Output: Title: New Members Joined
Summary: Ten new users j... -> Parsed: New Members Joined


Labeling Threads:   2%|▏         | 2/96 [00:03<02:25,  1.55s/thread]

DEBUG: Raw LLM Output: Title: New Members Joined
Summary: Multiple indivi... -> Parsed: New Members Joined


Labeling Threads:   3%|▎         | 3/96 [00:03<01:55,  1.24s/thread]

...

DEBUG: Raw LLM Output: Title: Group Welcome and Appreciation
Summary: A g... -> Parsed: Group Welcome and Appreciation


Labeling Threads:  99%|█████████▉| 95/96 [01:56<00:01,  1.39s/thread]

DEBUG: Raw LLM Output: Title: Same Same Same
Summary: Friends joking abou... -> Parsed: Same Same Same


Labeling Threads: 100%|██████████| 96/96 [01:57<00:00,  1.22s/thread]
INFO:core.processor:_labels_to_threads: labeling complete
INFO:core.processor:run_batch: threads after labels=96 memberships_total=9102
INFO:core.processor:run_batch: computing thread reps for tids=96
INFO:core.processor:run_batch: thread reps shape=(96, 384) dtype=float32
INFO:core.processor:run_batch: stored thread reps space=thread:centroid count=96
INFO:core.processor:run_batch: done


DEBUG: Raw LLM Output: Title: No Issues Found
Summary: A conversation wit... -> Parsed: No Issues Found


In [33]:
processor.threads.all()

[Thread(id='thread_9c2a5232ad', title='New Members Joined', summary='Ten new users joined the group.', created_at=datetime.datetime(2026, 1, 9, 12, 5, 20, 28910), updated_at=datetime.datetime(2020, 7, 18, 17, 35), metadata={}),
 Thread(id='thread_8f5859431f', title='New Members Joined', summary='Multiple individuals have joined the group using the invite link.', created_at=datetime.datetime(2026, 1, 9, 12, 5, 20, 28922), updated_at=datetime.datetime(2020, 4, 7, 20, 0), metadata={}),
 Thread(id='thread_ea775b95ce', title='Help Desk Chat', summary='Technical support conversation.', created_at=datetime.datetime(2026, 1, 9, 12, 5, 20, 28928), updated_at=datetime.datetime(2020, 9, 30, 10, 58), metadata={}),
 Thread(id='thread_80918f9564', title='Unidentified Voice', summary='Unidentified voice calls a stranger.', created_at=datetime.datetime(2026, 1, 9, 12, 5, 20, 28933), updated_at=datetime.datetime(2020, 10, 1, 10, 42), metadata={}),
 Thread(id='thread_58e2b692c2', title='Deleted Conversa

In [34]:
processor.memberships

<MembershipStore with 9102 memberships>

In [35]:
processor.messages

<MessageStore with 13655 messages>

In [36]:
import psutil, os
p = psutil.Process(os.getpid())
print("RSS GB:", p.memory_info().rss / 1e9)

RSS GB: 5.181054976


In [37]:
processor.messages.all()[1]

Message(id='m1', timestamp=datetime.datetime(2020, 1, 24, 20, 25), user='group_notification', text='Tanay Kamath (TSEC, CS) created group "CODERS👨\u200d💻👩\u200d💻🖥💻" ', metadata={})

### Visualisations

In [38]:
import pandas as pd
from sklearn.decomposition import PCA
import plotly.express as px

# 1. Retrieve Data
all_messages = processor.messages.all()
mids = processor.messages.ids()

# 2. Get Embeddings
_, X_cluster = processor.embeddings.get_matrix("msg:cluster")

# 3. Map Message IDs to Thread Info
mid_to_tid = {}
mid_to_title = {}

# Initialize defaults (Noise)
for mid in mids:
    mid_to_tid[mid] = "noise"
    mid_to_title[mid] = "Noise / Unassigned"

# Populate with active thread data
for m in processor.memberships._all:
    if m.status == 'active':
        thread = processor.threads.get(m.thread_id)

        mid_to_tid[m.message_id] = thread.id
        mid_to_title[m.message_id] = thread.title

# Construct DataFrame
df_viz = pd.DataFrame({
    'message_id': mids,
    'date_time': [m.timestamp for m in all_messages],
    'user': [m.user for m in all_messages],
    'message': [m.text for m in all_messages],
    'thread_id': [mid_to_tid[mid] for mid in mids],
    'thread_title': [mid_to_title[mid] for mid in mids]
})

# Create a "Unique Display Label"
# This ensures "Discussion (#123)" and "Discussion (#456)" get different colors
def make_unique_label(row):
    if row['thread_id'] == 'noise':
        return 'Noise'
    # Append short ID hash to ensure uniqueness in the legend
    short_id = row['thread_id'].split('_')[-1][:4]
    return f"{row['thread_title']} ({short_id})"

df_viz['legend_label'] = df_viz.apply(make_unique_label, axis=1)

print(f"Dataframe prepared with {len(df_viz)} rows.")

Dataframe prepared with 13655 rows.


In [39]:
# PCA & Plotting
pca = PCA(n_components=2)
viz_pca = pca.fit_transform(X_cluster)

df_viz['x'] = viz_pca[:, 0]
df_viz['y'] = viz_pca[:, 1]

fig = px.scatter(
    df_viz,
    x='x',
    y='y',
    color='legend_label',

    # Show the clean title in the hover box
    hover_data={
        'legend_label': False,
        'thread_title': True,
        'user': True,
        'message': True,
        'x': False,
        'y': False
    },
    title="Chat Topics: Distinct Threads (Colored by Unique ID)",
    template="plotly_dark"
)

# Visual polish
fig.update_traces(marker=dict(size=6, opacity=0.8))
fig.show()

In [41]:
import plotly.express as px

# # Filter out Noise
# df_timeline = df_viz[df_viz['thread_id'] != 'noise'].copy()

# Sort by Thread Title so the Y-axis is organized alphabetically (or you can sort by time)
df_timeline = df_viz.sort_values('thread_title')

# Plot
fig = px.scatter(
    df_timeline,
    x='date_time',
    y='thread_title',
    color='legend_label',
    hover_data=['user', 'message'],
    title="Timeline of Topics: When did conversations happen?",
    template="plotly_dark",
    height=800
)

fig.update_traces(marker=dict(size=6))
fig.update_layout(showlegend=False) # Hide legend if there are too many topics
fig.show()